This Jupyter Notebook Has all the code used to process the Visualization for the ICICLE FOOD FLOWS Reseach Project

The main library used for the visualization is Pydeck:
https://deckgl.readthedocs.io/en/latest/

This Code is the Sample Visualization provided by pydeck with all the waypoints in the trips layer

In [ ]:
import pydeck as pdk 
import pandas as pd
from IPython.core.display import display

"""
TripsLayer
==========

Plot of a single vehicle trip within San Francisco, fading in from the origin.

Adapted from a deck.gl documentation example.
"""
TRIPS_LAYER_DATA = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/website/sf.trips.json"  # noqa

df = pd.read_json(TRIPS_LAYER_DATA)

df["coordinates"] = df["waypoints"].apply(lambda f: [item["coordinates"] for item in f])
df["timestamps"] = df["waypoints"].apply(lambda f: [item["timestamp"] - 1554772579000 for item in f])

df.drop(["waypoints"], axis=1, inplace=True)

layer = pdk.Layer(
    "TripsLayer",
    df,
    get_path="coordinates",
    get_timestamps="timestamps",
    get_color=[253, 128, 93],
    opacity=0.8,
    width_min_pixels=5,
    rounded=True,
    trail_length=600,
    current_time=500,
)

view_state = pdk.ViewState(latitude=37.7749295, longitude=-122.4194155, zoom=11, bearing=0, pitch=45)

# Render
r = pdk.Deck(layers=[layer], initial_view_state=view_state)
r.to_html("trips_layer.html")

However in the FAF data set, we only have the origin and the destination, so here is what the visualization will look like without the way points.

In [ ]:
from IPython.core.display import display
import pydeck as pdk 
import pandas as pd

TRIPS_LAYER_DATA = "https://raw.githubusercontent.com/visgl/deck.gl-data/master/website/sf.trips.json"  # noqa

df = pd.read_json(TRIPS_LAYER_DATA)

df["coordinates"] = df["waypoints"].apply(lambda f: [item["coordinates"] for item in f])
df["timestamps"] = df["waypoints"].apply(lambda f: [item["timestamp"] - 1554772579000 for item in f])

df.drop(["waypoints"], axis=1, inplace=True)

# iterate over each row in the DataFrame and modify the 'coordinates' and 'timestamps' columns
for index, row in df.iterrows():

    # keep only the first and last coordinates
    df.at[index, 'coordinates'] = [row['coordinates'][0], row['coordinates'][-1]]
    
    # keep only the first and last timestamps
    df.at[index, 'timestamps'] = [row['timestamps'][0], row['timestamps'][-1]]

# define the TripsLayer with balanced speed and visibility
layer = pdk.Layer(
    "TripsLayer",
    df,
    get_path="coordinates",
    get_timestamps="timestamps",
    get_color=[255, 0, 0],  # bright red for high contrast
    opacity=1,  # maximum brightness
    width_min_pixels=7,  # thicker lines for better visibility
    rounded=True,
    trail_length=800,  # longer trail for better persistence
    current_time=1200,  # adjusted for smooth motion
)

# set up the initial view
view_state = pdk.ViewState(
    latitude=37.7749295, longitude=-122.4194155, zoom=11, bearing=0, pitch=45
)

# render the map
r = pdk.Deck(layers=[layer], initial_view_state=view_state)

# display the map in Jupyter Notebook
display(r.show())


This is a sample visualization of one of the trips from Orlando to Houston with hardcoded co-ordinates

In [ ]:
import pandas as pd
import pydeck as pdk
from IPython.core.display import display

trip_data = {
    "trip_id": [1],
    "coordinates": [[
        [-81.3792, 28.5383],
        [-95.3698, 29.7604]
    ]],
    "timestamps": [[0, 10]]
}

df = pd.DataFrame(trip_data)

layer = pdk.Layer(
    "TripsLayer",
    df,
    get_path="coordinates",
    get_timestamps="timestamps",
    get_color=[255, 0, 0],
    opacity=1,
    width_min_pixels=3,
    rounded=True,
    trail_length=150,
    current_time=50,
)

view_state = pdk.ViewState(
    latitude=39.8283, longitude=-98.5795, zoom=3, bearing=0, pitch=45
)

r = pdk.Deck(layers=[layer], initial_view_state=view_state)

display(r.show())


This is the code used to clean the sctg file by removing duplicate destination and source (Columns A and B) values along with 0 value for K, L, M columns

In [ ]:
import pandas as pd

# UNCOMMENT THE PATH FOR THIS TO WORK

#file_path = "/Users/devpaul/Desktop/ON-GOING PROJECTS/699/Food-Flow-Project/files/sctg_2_processed_files/processed_sctg_2_1.xlsx"
#df = pd.read_excel(file_path)

# Condition 1: Remove rows where columns B and C (index 1 and 2) have the same value
df = df[df.iloc[:, 1] != df.iloc[:, 2]]

# Condition 2: Remove rows where columns K, L, and M (index 10, 11, 12) are all 0
df = df[~((df.iloc[:, 10] == 0) & (df.iloc[:, 11] == 0) & (df.iloc[:, 12] == 0))]

# saving the cleaned data back to Excel
df.to_excel("cleaned_sctg_2_1.xlsx", index=False)

print("Processing complete. Cleaned file saved as 'cleaned_sctg_2_1.xlsx'.")


This is the first Visualization of the SCTG_2_1 FAF Data 

In [39]:
import pandas as pd
import geopandas as gpd
import pydeck as pdk


# Loading and Cleaning the sctg_2 file
sctg_2_1 = pd.read_excel("../files/sctg_2_processed_files/cleaned_sctg_2_1.xlsx")
# Convert `dms_orig` and `dms_dest` to integers and then format them with a leading zero if necessary
sctg_2_1['dms_orig'] = sctg_2_1['dms_orig'].astype(int).apply(lambda x: f"{x:03d}")
sctg_2_1['dms_dest'] = sctg_2_1['dms_dest'].astype(int).apply(lambda x: f"{x:03d}")

# Loading and Cleaning the shp file
shp = gpd.read_file("../files/2017_CFS_Metro_Areas_with_FAF/2017_CFS_Metro_Areas_with_FAF.shp")
#shp = shp.to_crs(crs=3857)
shp['centroid'] = shp['geometry'].centroid
shp = shp[['FAF_Zone', 'centroid']]

# Adding the centroid column for the origin and destination 
sctg_2_1['dms_orig_centroid'] = sctg_2_1['dms_orig'].map(shp.set_index('FAF_Zone')['centroid'])
sctg_2_1['dms_dest_centroid'] = sctg_2_1['dms_dest'].map(shp.set_index('FAF_Zone')['centroid'])

test = sctg_2_1.iloc[67]

def convert_sctg_to_trip(sctg_df, num_elements=None):
    """Converts sctg DataFrame to trip data format."""
    if num_elements:
        sctg_df = sctg_df.head(num_elements)

    trip_data = {
        "coordinates": [
            [[point.x, point.y], [dest.x, dest.y]]
            for point, dest in zip(sctg_df["dms_orig_centroid"], sctg_df["dms_dest_centroid"])
        ],
        "timestamps": [[0, 10]] * len(sctg_df)
    }

    return pd.DataFrame(trip_data)

trip_df = convert_sctg_to_trip(sctg_2_1, num_elements=1)

# Create trip data (coordinates, timestamps)
trip_data = {
    "coordinates": [[
        [-92.43924, 34.89977],
        [-96.8651, 32.88251]
    ]],
    "timestamps": [[0, 10]]
}

# Create the TripsLayer
trip_layer = pdk.Layer(
    "TripsLayer",
    trip_df,
    get_path="coordinates",
    get_timestamps="timestamps",
    get_color=[255, 0, 0],
    opacity=1,
    width_min_pixels=3,
    rounded=True,
    trail_length=150,
    current_time=50,
)

# Set up the view state as the center of the US
view_state = pdk.ViewState(
    latitude=39.8283, longitude=-98.5795, zoom=3, bearing=0, pitch=45
)

# Create the deck with both layers
r = pdk.Deck(
    layers=[trip_layer],
    initial_view_state=view_state
)

# Display the map
display(r.show())

/var/folders/wn/3whdxj5s3t530n5pvzzm87kh0000gn/T/ipykernel_24016/763359535.py:15: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  shp['centroid'] = shp['geometry'].centroid


In [43]:
import pandas as pd

def convert_sctg_to_trip(sctg_df, num_elements=None):
    """Converts sctg DataFrame to trip data format."""
    if num_elements:
        sctg_df = sctg_df.head(num_elements)

    trip_data = {
        "coordinates": [
            [[point.x, point.y], [dest.x, dest.y]]
            for point, dest in zip(sctg_df["dms_orig_centroid"], sctg_df["dms_dest_centroid"])
        ],
        "timestamps": [[0, 2]] * len(sctg_df)
    }

    return pd.DataFrame(trip_data)

# Example usage
trip_df = convert_sctg_to_trip(sctg_2_1, num_elements=10000)  # Adjust num_elements as needed

# Display full output
pd.set_option("display.max_columns", None)  # Show all columns
pd.set_option("display.max_colwidth", None)  # Prevent truncation of cell contents
pd.set_option("display.expand_frame_repr", False)  # Prevent column wrapping

print(trip_df)


# Create the TripsLayer
trip_layer = pdk.Layer(
    "TripsLayer",
    trip_df,
    get_path="coordinates",
    get_timestamps="timestamps",
    get_color= [255, 165, 0],
    opacity=0.6,
    width_min_pixels=3,
    rounded=True,
    trail_length=150,
    current_time=2,
)

# Set up the view state as the center of the US
view_state = pdk.ViewState(
    latitude=39.8283, longitude=-98.5795, zoom=3, bearing=0, pitch=45
)

# Create the deck with both layers
r = pdk.Deck(
    layers=[trip_layer],
    initial_view_state=view_state
)

# Display the map
display(r.show())


                                                                                 coordinates timestamps
0         [[-86.62142653051761, 33.42022725559913], [-86.79257359850203, 32.80456591304329]]     [0, 2]
1          [[-86.62142653051761, 33.42022725559913], [-83.12784531415367, 28.7029767386201]]     [0, 2]
2          [[-86.62142653051761, 33.42022725559913], [-84.3083014500991, 33.73601072682931]]     [0, 2]
3         [[-86.62142653051761, 33.42022725559913], [-83.32679868637767, 32.37514739839301]]     [0, 2]
4        [[-86.62142653051761, 33.42022725559913], [-89.65335940955671, 32.712892273199785]]     [0, 2]
5          [[-86.62142653051761, 33.42022725559913], [-78.8796273780312, 35.41920301388205]]     [0, 2]
6         [[-86.62142653051761, 33.42022725559913], [-86.76276903034223, 35.95688536561265]]     [0, 2]
7        [[-86.62142653051761, 33.42022725559913], [-86.44721480774969, 35.819483018525844]]     [0, 2]
8        [[-87.95034404855788, 30.671800040924573], [-86.7925735

In [38]:
len(sctg_2_1)

17364

In [41]:
len(sctg_2_1)

8130